/content


In [1]:
!apt -y install -qq aria2
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/text_model/adapter_config.json -d /content/joy/text_model -o adapter_config.json
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/text_model/adapter_model.safetensors -d /content/joy/text_model -o adapter_model.safetensors
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/clip_model.pt -d /content/joy -o clip_model.pt
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/raw/main/config.yaml -d /content/joy -o config.yaml
!aria2c --console-log-level=error -c -x 16 -s 16 -k 1M https://huggingface.co/camenduru/joy-caption-alpha-one/resolve/main/image_adapter.pt -d /content/joy -o image_adapter.pt

!pip install peft bitsandbytes

The following additional packages will be installed:
  libaria2-0 libc-ares2
The following NEW packages will be installed:
  aria2 libaria2-0 libc-ares2
0 upgraded, 3 newly installed, 0 to remove and 18 not upgraded.
Need to get 1,513 kB of archives.
After this operation, 5,441 kB of additional disk space will be used.
Selecting previously unselected package libc-ares2:amd64.
(Reading database ... 124950 files and directories currently installed.)
Preparing to unpack .../libc-ares2_1.18.1-1ubuntu0.22.04.3_amd64.deb ...
Unpacking libc-ares2:amd64 (1.18.1-1ubuntu0.22.04.3) ...
Selecting previously unselected package libaria2-0:amd64.
Preparing to unpack .../libaria2-0_1.36.0-1_amd64.deb ...
Unpacking libaria2-0:amd64 (1.36.0-1) ...
Selecting previously unselected package aria2.
Preparing to unpack .../aria2_1.36.0-1_amd64.deb ...
Unpacking aria2 (1.36.0-1) ...
Setting up libc-ares2:amd64 (1.18.1-1ubuntu0.22.04.3) ...
Setting up libaria2-0:amd64 (1.36.0-1) ...
Setting up aria2 (1.36.0-1) 

In [2]:
from huggingface_hub import InferenceClient
from torch import nn
from transformers import AutoModel, AutoProcessor, AutoTokenizer, PreTrainedTokenizer, PreTrainedTokenizerFast, AutoModelForCausalLM
import torch
import torch.amp.autocast_mode
from PIL import Image
import os
import torchvision.transforms.functional as TVF

CLIP_PATH = "google/siglip-so400m-patch14-384"
MODEL_PATH = "unsloth/Meta-Llama-3.1-8B"
CAPTION_TYPE_MAP = {
    ("descriptive", "formal", False, False): ["Describe the image in 400 words"],
    ("descriptive", "formal", False, True): ["Write a descriptive caption for this image in a formal tone within {word_count} words."],
    ("descriptive", "formal", True, False): ["Write a {length} descriptive caption for this image in a formal tone."],
    ("descriptive", "informal", False, False): ["Write a descriptive caption for this image in a casual tone."],
    ("descriptive", "informal", False, True): ["Write a descriptive caption for this image in a casual tone within {word_count} words."],
    ("descriptive", "informal", True, False): ["Write a {length} descriptive caption for this image in a casual tone."],
    ("training_prompt", "formal", False, False): ["Write a stable diffusion prompt for this image."],
    ("training_prompt", "formal", False, True): ["Write a stable diffusion prompt for this image within {word_count} words."],
    ("training_prompt", "formal", True, False): ["Write a {length} stable diffusion prompt for this image."],
    ("rng-tags", "formal", False, False): ["Write a list of Booru tags for this image."],
    ("rng-tags", "formal", False, True): ["Write a list of Booru tags for this image within {word_count} words."],
    ("rng-tags", "formal", True, False): ["Write a {length} list of Booru tags for this image."],
}

class ImageAdapter(nn.Module):
	def __init__(self, input_features: int, output_features: int, ln1: bool, pos_emb: bool, num_image_tokens: int, deep_extract: bool):
		super().__init__()
		self.deep_extract = deep_extract
		if self.deep_extract:
			input_features = input_features * 5
		self.linear1 = nn.Linear(input_features, output_features)
		self.activation = nn.GELU()
		self.linear2 = nn.Linear(output_features, output_features)
		self.ln1 = nn.Identity() if not ln1 else nn.LayerNorm(input_features)
		self.pos_emb = None if not pos_emb else nn.Parameter(torch.zeros(num_image_tokens, input_features))
		self.other_tokens = nn.Embedding(3, output_features)
		self.other_tokens.weight.data.normal_(mean=0.0, std=0.02)   # Matches HF's implementation of llama3
	def forward(self, vision_outputs: torch.Tensor):
		if self.deep_extract:
			x = torch.concat((
				vision_outputs[-2],
				vision_outputs[3],
				vision_outputs[7],
				vision_outputs[13],
				vision_outputs[20],
			), dim=-1)
			assert len(x.shape) == 3, f"Expected 3, got {len(x.shape)}"  # batch, tokens, features
			assert x.shape[-1] == vision_outputs[-2].shape[-1] * 5, f"Expected {vision_outputs[-2].shape[-1] * 5}, got {x.shape[-1]}"
		else:
			x = vision_outputs[-2]
		x = self.ln1(x)
		if self.pos_emb is not None:
			assert x.shape[-2:] == self.pos_emb.shape, f"Expected {self.pos_emb.shape}, got {x.shape[-2:]}"
			x = x + self.pos_emb
		x = self.linear1(x)
		x = self.activation(x)
		x = self.linear2(x)
		other_tokens = self.other_tokens(torch.tensor([0, 1], device=self.other_tokens.weight.device).expand(x.shape[0], -1))
		assert other_tokens.shape == (x.shape[0], 2, x.shape[2]), f"Expected {(x.shape[0], 2, x.shape[2])}, got {other_tokens.shape}"
		x = torch.cat((other_tokens[:, 0:1], x, other_tokens[:, 1:2]), dim=1)
		return x
	def get_eot_embedding(self):
		return self.other_tokens(torch.tensor([2], device=self.other_tokens.weight.device)).squeeze(0)

clip_processor = AutoProcessor.from_pretrained(CLIP_PATH)
clip_model = AutoModel.from_pretrained(CLIP_PATH)
clip_model = clip_model.vision_model
checkpoint = torch.load("/content/joy/clip_model.pt", map_location='cpu')
checkpoint = {k.replace("_orig_mod.module.", ""): v for k, v in checkpoint.items()}
clip_model.load_state_dict(checkpoint)
# del checkpoint
clip_model.eval()
clip_model.requires_grad_(False)
clip_model.to("cuda")
tokenizer = AutoTokenizer.from_pretrained(MODEL_PATH, use_fast=False)
assert isinstance(tokenizer, PreTrainedTokenizer) or isinstance(tokenizer, PreTrainedTokenizerFast), f"Tokenizer is of type {type(tokenizer)}"
text_model = AutoModelForCausalLM.from_pretrained(MODEL_PATH, load_in_8bit=True, device_map="auto", torch_dtype=torch.bfloat16)
text_model.load_adapter("/content/joy/text_model")
text_model.eval()
image_adapter = ImageAdapter(clip_model.config.hidden_size, text_model.config.hidden_size, False, False, 38, False)
image_adapter.load_state_dict(torch.load("/content/joy/image_adapter.pt", map_location="cpu"))
image_adapter.eval()
image_adapter.to("cuda")

@torch.no_grad()
def stream_chat(input_image: Image.Image, caption_type: str, caption_tone: str, caption_length: str | int) -> str:
    torch.cuda.empty_cache()
    length = None if caption_length == "any" else caption_length
    if isinstance(length, str):
        try:
            length = int(length)
        except ValueError:
            pass
    if caption_type == "rng-tags" or caption_type == "training_prompt":
        caption_tone = "formal"
    prompt_key = (caption_type, caption_tone, isinstance(length, str), isinstance(length, int))
    if prompt_key not in CAPTION_TYPE_MAP:
        raise ValueError(f"Invalid caption type: {prompt_key}")
    prompt_str = CAPTION_TYPE_MAP[prompt_key][0].format(length=length, word_count=length)
    print(f"Prompt: {prompt_str}")
    image = input_image.resize((384, 384), Image.LANCZOS)
    pixel_values = TVF.pil_to_tensor(image).unsqueeze(0) / 255.0
    pixel_values = TVF.normalize(pixel_values, [0.5], [0.5])
    pixel_values = pixel_values.to('cuda')
    prompt = tokenizer.encode(prompt_str, return_tensors='pt', padding=False, truncation=False, add_special_tokens=False)
    with torch.amp.autocast_mode.autocast('cuda', enabled=True):
        vision_outputs = clip_model(pixel_values=pixel_values, output_hidden_states=True)
        image_features = vision_outputs.hidden_states
        embedded_images = image_adapter(image_features)
        embedded_images = embedded_images.to('cuda')
    prompt_embeds = text_model.model.embed_tokens(prompt.to('cuda'))
    assert prompt_embeds.shape == (1, prompt.shape[1], text_model.config.hidden_size), f"Prompt shape is {prompt_embeds.shape}, expected {(1, prompt.shape[1], text_model.config.hidden_size)}"
    embedded_bos = text_model.model.embed_tokens(torch.tensor([[tokenizer.bos_token_id]], device=text_model.device, dtype=torch.int64))
    eot_embed = image_adapter.get_eot_embedding().unsqueeze(0).to(dtype=text_model.dtype)
    inputs_embeds = torch.cat([
        embedded_bos.expand(embedded_images.shape[0], -1, -1),
        embedded_images.to(dtype=embedded_bos.dtype),
        prompt_embeds.expand(embedded_images.shape[0], -1, -1),
        eot_embed.expand(embedded_images.shape[0], -1, -1),
    ], dim=1)
    input_ids = torch.cat([
        torch.tensor([[tokenizer.bos_token_id]], dtype=torch.long),
        torch.zeros((1, embedded_images.shape[1]), dtype=torch.long),
        prompt,
        torch.tensor([[tokenizer.convert_tokens_to_ids("<|eot_id|>")]], dtype=torch.long),
    ], dim=1).to('cuda')
    attention_mask = torch.ones_like(input_ids)
    generate_ids = text_model.generate(input_ids, inputs_embeds=inputs_embeds, attention_mask=attention_mask, max_new_tokens=300, do_sample=True, suppress_tokens=None)   # Uses the default which is temp=0.6, top_p=0.9
    generate_ids = generate_ids[:, input_ids.shape[1]:]
    if generate_ids[0][-1] == tokenizer.eos_token_id or generate_ids[0][-1] == tokenizer.convert_tokens_to_ids("<|eot_id|>"):
        generate_ids = generate_ids[:, :-1]
    caption = tokenizer.batch_decode(generate_ids, skip_special_tokens=False, clean_up_tokenization_spaces=False)[0]
    caption = f'{caption.strip()}'.replace('Prompt: Describe the image in 400 words','')
    return caption

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


preprocessor_config.json:   0%|          | 0.00/368 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/711 [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/798k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/409 [00:00<?, ?B/s]

...

model-00003-of-00004.safetensors:   0%|          | 0.00/4.92G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/1.17G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/230 [00:00<?, ?B/s]

<ipython-input-2-d7ae426ea27d>:83: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  image_adapter.load_state_dict(torch.load("/content/joy/image_adapter.pt", map_location="cpu"

In [3]:
import os
from PIL import Image
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)


tgt_directory = f'{home_directory}tmp'
my_mkdirs(f'{tgt_directory}')

tgt_folder = '/content/'
suffixes = ['.png', '.jpeg' , '.webp' , '.jpg']
num = 1
for filename in os.listdir(tgt_folder):
  for suffix in suffixes:
    if not filename.find(suffix)>-1: continue
    print(filename)
    %cd {home_directory}
    input_image = Image.open(f"{filename}").convert('RGB')
    %cd {tgt_directory}
    input_image.save(f'{162 + num}.png', "PNG")
    num = num+1

/content
2025-01-29 11.35.10_1.jpg
/content
/content/tmp
2025-01-29 11.15.21.webp
/content
/content/tmp
2025-01-29 11.01.18_6.jpg
/content
/content/tmp
2025-01-29 11.01.18_5.jpg
/content
/content/tmp
2012-05-15 22.22.14.jpg
/content
/content/tmp
2025-01-29 11.01.18_3.jpg
/content
/content/tmp
2025-01-29 11.01.23_3.jpg
/content
/content/tmp
2025-01-29 11.01.21_4.jpg
/content
/content/tmp
2025-01-29 11.01.20_2.jpg
/content
/content/tmp
2025-01-29 11.01.21_1.jpg
/content
/content/tmp
2013-01-14 01.03.06.jpg
/content
/content/tmp
2025-01-18 04.07.57_9.jpg
/content
/content/tmp
2025-01-29 11.01.18_1.jpg
/content
/content/tmp
2025-01-29 11.01.23_1.jpg
/content
/content/tmp
2025-01-29 11.01.22_2.jpg
/content
/content/tmp
2025-01-29 11.35.10_3.jpg
/content
/content/tmp
2025-01-29 11.01.23_2.jpg
/content
/content/tmp
2025-01-29 11.35.10_5.jpg
/content
/content/tmp
2025-01-29 11.01.22.jpg
/content
/content/tmp
2025-01-29 11.01.18_9.jpg
/content
/content/tmp
2025-01-29 11.01.20_1.jpg
/content
/co

In [ ]:
%cd /content/
import shutil
shutil.make_archive('prompts', 'zip', '/content/tmp')

/content


'/content/prompts.zip'

In [ ]:
from PIL import Image

# Open an existing image
#image = Image.open('new_york_city.jpg')

# Save the image in a different format


suffix = 'png'
for number in range(300):
  try:
    %cd /content/
    input_image = Image.open(f"/content/tmp/{number+1}.{suffix}").convert('RGB')
    caption = stream_chat(input_image, "descriptive", "formal", "any")
    %cd /content/tmp
    f = open(f"{number+1}.txt", "w")
    f.write(f'{caption}')
    f.close()
    print(f"...\n\n...caption for {number+1}.{suffix}\n\n...")
    print(caption)
  except:
    continue
#----#


/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/content
/

/usr/local/lib/python3.11/dist-packages/bitsandbytes/autograd/_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


In [ ]:
%cd /content/
import shutil
shutil.make_archive('prompts', 'zip', '/content/tmp')

/content


'/content/prompts.zip'

In [ ]:
#initialize
import torch
from safetensors.torch import load_file, save_file
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import torch
from safetensors.torch import load_file, save_file
import torch.nn as nn
from torch import linalg as LA
import os
import math
import random
import numpy as np
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# This method rescales a _lora to a given ratio. I haven't tested it
# yet but this is more or less how it works
def rescale_and_save(_lora , savefile_name, new_ratio):
    count = 0
    lora = {}
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    decimals = 6
    for key in _lora:
        if not f'{key}'.find('alpha') > -1: continue
        alpha = f'{key}'
        up = f'{key}'.replace('alpha' , 'lora_up.weight')
        down = f'{key}'.replace('alpha' , 'lora_down.weight')
        #------#
        rank = _lora[f'{down}'].shape[0]
        new_alpha = torch.tensor(new_ratio*rank).to(device = device , dtype=torch.float32)
        lora[up] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[up], decimals = decimals).to(device = device , dtype=torch.float32)
        lora[down] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[down], decimals = decimals).to(device = device , dtype=torch.float32)
        #-----#
        lora[alpha] = (new_alpha/_lora[alpha])*_lora[alpha].to(device = device , dtype=torch.float32)
        count = count + 3
        print(f'{count} / {NUM_ITEMS}')
    #--------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
  #-----------#

tgt = load_file("/content/drive/MyDrive/'Your Name (Makoto Shinkai)' - v3 - [STYLE] [LORA] [FLUX] - spectrum_0008 by 'AI_Characters'.safetensors")
for key in tgt:
  tgt[f'{key}'] = tgt[f'{key}'].to(device = device , dtype=torch.float32)


if False:
  for key in tgt:
    if f'{key}'.find('alpha')>-1: print(tgt[f'{key}'])
    print(f" {key} : {tgt[f'{key}'].shape}")

name = 'shinkai'
savefile_name = f'{name}.safetensors'
new_ratio = 0.5


if True:
  rescale_and_save(tgt , savefile_name, new_ratio)
    #(alpha/scale) = (32/16)

  tgt = load_file(f'{savefile_name}')
  for key in tgt:
    if f'{key}'.find('alpha')>-1: print(tgt[f'{key}'])
    print(f" {key} : {tgt[f'{key}'].shape}")

In [ ]:
import torch
from safetensors.torch import load_file, save_file
import torch.nn as nn
from torch import linalg as LA
import os
import math
import random
import numpy as np
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# filter_and_save
# Use this method to change the scale = (rank/alpha) value of a given _lora
# This method will also eliminate noise. All values < zero_threshold * e-6  will be set to 0
# in the delta_W of this LoRa. The processed LoRa will be saved as a .safetensor file in fp16
# The rank of the LoRa affect the file size. At rank 32 the filesize is 300 MB , at rank 16 the filesize is 150 MB and so on.
#
# When merging LoRa , it is important that
# a) the scale of all the merged LoRas are the same. I use the scale = (alpha/rank) = 0.5 at all times.
#    For rank 32 , the alpha must be 16 , for example.
#
# b) The rank of the merged LoRas should be 32 or below , any larger values might trigger a 'Out of Memory' error on Google Colab GPU:s
# --------------
# _lora - The lora which you wish to process
# savefile_name - The name of the savefile to be created. Make sure the savefile_name ends with the '.safetensors' suffix
# new_rank -  The rank you wish to set the LoRa to
# new_alpha - The alpha value you wish to set the LoRa to. For proper scaling ,
#             set the alpha value to half the value of the rank so (alpha/rank) = 0.5
#             This is a very common scale for trained LoRa
#
# zero_threshold - All values < zero_threshold * e-6  will be set to 0
# in the delta_W of this LoRa. This is useful to eliminate 'junk' in the output of the
# Lora when scaling it to strength above 0.8. A high zero_threshold will also make the Lora more compatible with other LoRa
# , at the expense of making the LoRa less true to the originally trained image output.
#
def filter_and_save(_lora , savefile_name, new_rank , new_alpha, zero_threshold):
    lora = {}
    count = 0
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    thresh = zero_threshold*0.000001 # 1e-6
    #-------#
    for key in _lora:
        if f'{key}'.find('alpha') > -1:
            lora[f'{key}'] = torch.tensor(new_alpha).to(device = device , dtype = torch.float32)
            count = count + 1
            print(f'{count} / {NUM_ITEMS}')
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#
        delta_W = torch.matmul(_lora[up],_lora[down]).to(device = device , dtype=torch.float32)
        #---#
        N = delta_W.numel()
        y = delta_W.flatten().to(device = device , dtype=torch.float32)
        values,indices = torch.sort(y, descending = False) # smallest -> largest elements
        y = torch.zeros(y.shape).to(device = device , dtype=torch.float32)
        y[indices[values>thresh]] = 1
        y[indices[values<-thresh]] = 1
        y = y.unflatten(0,delta_W.shape).to(device = device , dtype=torch.float32)
        delta_W = torch.mul(delta_W,y).to(device = device , dtype=torch.float32)
        #------#
        tmp={}
        tmp['u'], tmp['s'], tmp['Vh'] = torch.svd(delta_W)
        tmp['u'] = tmp['u'][:,: new_rank]
        tmp['s'] = tmp['s'][: new_rank]
        #-------#
        tmp['u'] = torch.round(torch.matmul(tmp['u'], torch.diag(tmp['s'])),decimals=6)
        tmp['Vh'] = torch.round(tmp['Vh'].t()[: new_rank,:],decimals=6)
        #-------#
        for key in tmp:tmp[f'{key}'] = tmp[f'{key}'].contiguous()
        lora[up] = tmp['u'].to(device = device , dtype=torch.float32)
        lora[down] = tmp['Vh'].to(device = device , dtype=torch.float32)
        #-------#
        count  = count  + 2
        print(f'{count} / {NUM_ITEMS}')
    #-------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in _lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
#--------#

# count_zeros
# Use this method to guage how large zero_threshold you should set for a given Lora.
# This function can serve as a 'preview' prior to running either the filter_and_save or
# merge_and_save methods. Since it does not use SVD to re-pack the LoRa
# , you can run this method on a non-GPU instance on the Colab
#-----------
# _lora - The lora which you wish to process
# zero_threshold - All values < zero_threshold * e-6  will be set to 0
def count_zeros(_lora, zero_threshold):
    count = 0
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    #-----#
    thresh = zero_threshold*0.000001 # 1e-6

    print(f'at zero_threshold = {zero_threshold}e-6 :')
    for key in _lora:
        if f'{key}'.find('alpha') > -1:
            count = count + 1
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#
        delta_W = torch.matmul(_lora[up],_lora[down]).to(device = device , dtype=torch.float32)
        N = delta_W.numel()
        y = delta_W.flatten().to(device = device , dtype=torch.float32)
        values,indices = torch.sort(y, descending = False) # smallest -> largest elements
        y = torch.ones(y.shape).to(device = device , dtype=torch.float32)
        y[indices[values>thresh]] = 0
        neg_pcnt  = round((100*torch.sum(y) / N).item(),2)
        y[indices[values<-thresh]] = 0
        count  = count  + 2
        pcnt  = round((100*torch.sum(y) / N).item(),2)
        neg_pcnt = round(neg_pcnt - pcnt,2) # remove zero % from neg_pcnt
        pos_pcnt = round(100- pcnt - neg_pcnt,2)
        print(f'at {count} / {NUM_ITEMS} : {pcnt} % zeros ,{pos_pcnt} % pos. , {neg_pcnt} % neg ')
    #------#
#-----#

# This method rescales a _lora to a given ratio. I haven't tested it
# But this is more or less how it works
def rescale_and_save(_lora , savefile_name, new_ratio):
    count = 0
    lora = {}
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    decimals = 6
    for key in _lora:
        if not f'{key}'.find('alpha') > -1: continue
        alpha = f'{key}'
        up = f'{key}'.replace('alpha' , 'lora_up')
        down = f'{key}'.replace('alpha' , 'lora_down')
        #------#
        rank = torch.matmul(_lora[up]*0,_lora[down]*0).shape[0]
        new_alpha = torch.tensor(new_ratio*rank).to(device = device , dtype=torch.float32)
        lora[up] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[up], decimals = decimals).to(device = device , dtype=torch.float32)
        lora[down] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[down], decimals = decimals).to(device = device , dtype=torch.float32)
        lora[alpha] = (new_alpha/_lora[alpha])*_lora[alpha].to(device = device , dtype=torch.float32)
        count = count + 3
        print(f'{count} / {NUM_ITEMS}')
    #--------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
  #-----------#

# merge_and_save
# This method uses a general neural net merging method known as TIES - which is an loose abbreviation for
# 'Trim Elect Sign & Merge' according to the paper : https://arxiv.org/pdf/2306.01708
#------------#
# _lora1 - The lora which you wish to process.
# _lora2 - The lora which you wish to process.
# _lora3 - The lora which you wish to process.

# NOTE about loras :
#_lora1 , _lora2  and lora_3 can have different ranks.
# Make sure the scale of all three loras are the same

#The scale is defined as (alpha/rank) and should be 0.5
# If the alpha value is too high or too low , for example if (alpha/rank) = 1
# then run rescale_and_save(_lora , savefile_name, new_alpha) , where new_alpha is given by the rank of the LoRa
# For example , a LoRa of rank 32  must have an alpha value of 16 for the scale = (alpha/rank) = 0.5 to be True

# However , make sure each lora rank is equal or below 32 ,
#or that the sum of ranks does not exceed 3*32 = 96 , to not exceed GPU requirements on Google Colab. Slightly higher values might be fine.
# Haven't tested it since I prefer merging LoRa at rank 32

# savefile_name - The name of the savefile to be created. Make sure the savefile_name ends with the '.safetensors' suffix
# new_rank -  The rank you wish to set the LoRa to
# new_alpha - The alpha value you wish to set the LoRa to. For proper scaling ,
#             set the alpha value to half the value of the rank so (alpha/rank) = 0.5
#             This is a very common scale for trained LoRa
#
# zero_threshold - All values < zero_threshold * e-6  will be set to 0
# in the delta_W of this LoRa. This is useful to eliminate 'junk' in the output of the
# Lora when scaling it to strength above 0.8. A high zero_threshold will also make the Lora more compatible with other LoRa
import torch
from safetensors.torch import load_file, save_file
import torch.nn as nn
from torch import linalg as LA
import os
import math
import random
import numpy as np
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# filter_and_save
# Use this method to change the scale = (rank/alpha) value of a given _lora
# This method will also eliminate noise. All values < zero_threshold * e-6  will be set to 0
# in the delta_W of this LoRa. The processed LoRa will be saved as a .safetensor file in fp16
# The rank of the LoRa affect the file size. At rank 32 the filesize is 300 MB , at rank 16 the filesize is 150 MB and so on.
#
# When merging LoRa , it is important that
# a) the scale of all the merged LoRas are the same. I use the scale = (alpha/rank) = 0.5 at all times.
#    For rank 32 , the alpha must be 16 , for example.
#
# b) The rank of the merged LoRas should be 32 or below , any larger values might trigger a 'Out of Memory' error on Google Colab GPU:s
# --------------
# _lora - The lora which you wish to process
# savefile_name - The name of the savefile to be created. Make sure the savefile_name ends with the '.safetensors' suffix
# new_rank -  The rank you wish to set the LoRa to
# new_alpha - The alpha value you wish to set the LoRa to. For proper scaling ,
#             set the alpha value to half the value of the rank so (alpha/rank) = 0.5
#             This is a very common scale for trained LoRa
#
# zero_threshold - All values < zero_threshold * e-6  will be set to 0
# in the delta_W of this LoRa. This is useful to eliminate 'junk' in the output of the
# Lora when scaling it to strength above 0.8. A high zero_threshold will also make the Lora more compatible with other LoRa
# , at the expense of making the LoRa less true to the originally trained image output.
#
def filter_and_save(_lora , savefile_name, new_rank , new_alpha, zero_threshold):
    lora = {}
    count = 0
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    thresh = zero_threshold*0.000001 # 1e-6
    #-------#
    for key in _lora:
        if f'{key}'.find('alpha') > -1:
            lora[f'{key}'] = torch.tensor(new_alpha).to(device = device , dtype = torch.float32)
            count = count + 1
            print(f'{count} / {NUM_ITEMS}')
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#
        delta_W = torch.matmul(_lora[up],_lora[down]).to(device = device , dtype=torch.float32)
        #---#
        N = delta_W.numel()
        y = delta_W.flatten().to(device = device , dtype=torch.float32)
        values,indices = torch.sort(y, descending = False) # smallest -> largest elements
        y = torch.zeros(y.shape).to(device = device , dtype=torch.float32)
        y[indices[values>thresh]] = 1
        y[indices[values<-thresh]] = 1
        y = y.unflatten(0,delta_W.shape).to(device = device , dtype=torch.float32)
        delta_W = torch.mul(delta_W,y).to(device = device , dtype=torch.float32)
        #------#
        tmp={}
        tmp['u'], tmp['s'], tmp['Vh'] = torch.svd(delta_W)
        tmp['u'] = tmp['u'][:,: new_rank]
        tmp['s'] = tmp['s'][: new_rank]
        #-------#
        tmp['u'] = torch.round(torch.matmul(tmp['u'], torch.diag(tmp['s'])),decimals=6)
        tmp['Vh'] = torch.round(tmp['Vh'].t()[: new_rank,:],decimals=6)
        #-------#
        for key in tmp:tmp[f'{key}'] = tmp[f'{key}'].contiguous()
        lora[up] = tmp['u'].to(device = device , dtype=torch.float32)
        lora[down] = tmp['Vh'].to(device = device , dtype=torch.float32)
        #-------#
        count  = count  + 2
        print(f'{count} / {NUM_ITEMS}  , rank {_lora[down].shape[0]}')
    #-------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in _lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
#--------#

# count_zeros
# Use this method to guage how large zero_threshold you should set for a given Lora.
# This function can serve as a 'preview' prior to running either the filter_and_save or
# merge_and_save methods. Since it does not use SVD to re-pack the LoRa
# , you can run this method on a non-GPU instance on the Colab
#-----------
# _lora - The lora which you wish to process
# zero_threshold - All values < zero_threshold * e-6  will be set to 0
def count_zeros(_lora, zero_threshold):
    count = 0
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    #-----#
    thresh = zero_threshold*0.000001 # 1e-6

    print(f'at zero_threshold = {zero_threshold}e-6 :')
    for key in _lora:
        if f'{key}'.find('alpha') > -1:
            count = count + 1
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#
        delta_W = torch.matmul(_lora[up],_lora[down]).to(device = device , dtype=torch.float32)
        N = delta_W.numel()
        y = delta_W.flatten().to(device = device , dtype=torch.float32)
        values,indices = torch.sort(y, descending = False) # smallest -> largest elements
        y = torch.ones(y.shape).to(device = device , dtype=torch.float32)
        y[indices[values>thresh]] = 0
        neg_pcnt  = round((100*torch.sum(y) / N).item(),2)
        y[indices[values<-thresh]] = 0
        count  = count  + 2
        pcnt  = round((100*torch.sum(y) / N).item(),2)
        neg_pcnt = round(neg_pcnt - pcnt,2) # remove zero % from neg_pcnt
        pos_pcnt = round(100- pcnt - neg_pcnt,2)
        print(f'at {count} / {NUM_ITEMS} : {pcnt} % zeros ,{pos_pcnt} % pos. , {neg_pcnt} % neg ')
    #------#
#-----#

# This method rescales a _lora to a given ratio. I haven't tested it
# yet but this is more or less how it works
def rescale_and_save(_lora , savefile_name, new_ratio):
    count = 0
    lora = {}
    for key in _lora:count = count + 1
    NUM_ITEMS = count
    count = 0
    decimals = 6
    for key in _lora:
        if not f'{key}'.find('alpha') > -1: continue
        alpha = f'{key}'
        up = f'{key}'.replace('alpha' , 'lora_up')
        down = f'{key}'.replace('alpha' , 'lora_down')
        #------#
        rank = lora[down].shape[0]
        new_alpha = torch.tensor(new_ratio*rank).to(device = device , dtype=torch.float32)
        lora[up] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[up], decimals = decimals).to(device = device , dtype=torch.float32)
        lora[down] = torch.round(torch.sqrt(_lora[alpha]/new_alpha)*_lora[down], decimals = decimals).to(device = device , dtype=torch.float32)
        lora[alpha] = (new_alpha/_lora[alpha])*_lora[alpha].to(device = device , dtype=torch.float32)
        count = count + 3
        print(f'{count} / {NUM_ITEMS}')
    #--------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
  #-----------#

# merge_and_save
# This method uses a general neural net merging method known as TIES - which is an loose abbreviation for
# 'Trim Elect Sign & Merge' according to the paper : https://arxiv.org/pdf/2306.01708
#------------#
# _lora1 - The lora which you wish to process.
# _lora2 - The lora which you wish to process.
# _lora3 - The lora which you wish to process.

# NOTE about loras :
#_lora1 , _lora2  and lora_3 can have different ranks.
# Make sure the scale of all three loras are the same

#The scale is defined as (alpha/rank) and should be 0.5
# If the alpha value is too high or too low , for example if (alpha/rank) = 1
# then run rescale_and_save(_lora , savefile_name, new_alpha) , where new_alpha is given by the rank of the LoRa
# For example , a LoRa of rank 32  must have an alpha value of 16 for the scale = (alpha/rank) = 0.5 to be True

# Make sure the sum of ranks for _lora1,_lora2 and _lora3 does not exceed 3*32 = 96 , to not exceed GPU requirements on Google Colab. Slightly higher values might be fine.
# Haven't tested it since I prefer merging LoRa at rank 32

# savefile_name - The name of the savefile to be created. Make sure the savefile_name ends with the '.safetensors' suffix
# new_rank -  The rank you wish to set the LoRa to
# new_alpha - The alpha value you wish to set the LoRa to. For proper scaling ,
#             set the alpha value to half the value of the rank so (alpha/rank) = 0.5
#             This is a very common scale for trained LoRa
#
# zero_threshold - All values < zero_threshold * e-6  will be set to 0
# in the delta_W of this LoRa. This is useful to eliminate 'junk' persists in the delta_W after training. A high resolution size will also make the Lora more compatible with other LoRa
# , at the expense of making the LoRa less true to the originally trained image output.
def merge_and_save(_lora1 , _lora2 , _lora3, savefile_name, new_rank , new_alpha, zero_threshold):
    lora = {}



    count = 0
    for key in _lora1:count = count + 1
    NUM_ITEMS = count
    count = 0
    thresh = zero_threshold*0.000001 # 1e-6
    decimals = 2

    #-------#
    for key in _lora1:
        if not key in _lora2: continue
        if not key in _lora3: continue
        if f'{key}'.find('alpha') > -1:
            lora[f'{key}'] = torch.tensor(new_alpha).to(device = device , dtype = torch.float32)
            count = count + 1
            print(f'{count} / {NUM_ITEMS}')
            continue
        #------#
        if not f'{key}'.find('lora_down') > -1: continue
        up = f'{key}'.replace('lora_down' , 'lora_up')
        down = f'{key}'
        #-------#

        # Setup
        delta_W = torch.matmul(_lora1[up]*0,_lora1[down]*0).to(device = device, dtype=torch.float32)
        tgt_shape = delta_W.shape
        N = delta_W.numel()
        delta_W = torch.zeros(N).to(device = device , dtype=torch.float32)
        #-----#

        #Positives
        Y = torch.zeros(3,N).to(device = device , dtype=torch.float32)
        Y[0] = torch.matmul(_lora1[up],_lora1[down]).flatten().to(device = device , dtype=torch.float32)
        Y[1] = torch.matmul(_lora2[up],_lora2[down]).flatten().to(device = device , dtype=torch.float32)
        Y[2] = torch.matmul(_lora3[up],_lora3[down]).flatten().to(device = device , dtype=torch.float32)
        Y[torch.abs(Y)<thresh] = 0 #Trim
        Y = torch.round(Y,decimals=decimals).t()
        num = torch.sum(Y>0,dim=1) + 0.001
        elect = torch.sum(Y<0,dim=1) + 0.001
        elect = (num>=elect)
        Y[Y<0] = 0
        Y = torch.sum(Y, dim=1).to(device = device , dtype=torch.float32)
        delta_W[elect] = torch.round((Y[elect]/num[elect]),decimals=decimals).to(device = device , dtype=torch.float32)
        #-----#

        #Negatives
        Y = torch.zeros(3,N).to(device = device , dtype=torch.float32)
        Y[0] = torch.matmul(_lora1[up],_lora1[down]).flatten().to(device = device , dtype=torch.float32)
        Y[1] = torch.matmul(_lora2[up],_lora2[down]).flatten().to(device = device , dtype=torch.float32)
        Y[2] = torch.matmul(_lora3[up],_lora3[down]).flatten().to(device = device , dtype=torch.float32)
        Y[torch.abs(Y)<thresh] = 0 #Trim
        Y = torch.round(Y,decimals=decimals).t()
        num = torch.sum(Y<0,dim=1) + 0.1  # <-- to prevent divide by 0
        elect = torch.sum(Y>0,dim=1) + 0.1
        elect = (elect<num)
        Y[Y>0] = 0
        Y = torch.sum(Y, dim=1).to(device = device , dtype=torch.float32)
        delta_W[elect] = torch.round(Y[elect]/num[elect],decimals=decimals).to(device = device , dtype=torch.float32)
        #----#

        # Free up memory prior to SVD
        delta_W = delta_W.unflatten(0,tgt_shape).to(device = device , dtype=torch.float32)
        delta_W = delta_W.clone().detach()
        Y = {}
        num = {}
        elect = {}
        #-----#

        # Run SVD (Single Value Decomposition)
        #to get the new lora_up and lora_down for delta_W
        tmp={}
        tmp['u'], tmp['s'], tmp['Vh'] = torch.svd(delta_W)
        tmp['u'] = tmp['u'][:,: new_rank]
        tmp['s'] = tmp['s'][: new_rank]
        tmp['u'] = torch.matmul(tmp['u'], torch.diag(tmp['s']))
        tmp['Vh'] = tmp['Vh'].t()[: new_rank,:]
        for key in tmp:tmp[f'{key}'] = tmp[f'{key}'].contiguous()
        lora[up] = torch.round(tmp['u'],decimals=decimals).to(device = device , dtype=torch.float32)
        lora[down] = torch.round(tmp['Vh'],decimals=decimals).to(device = device , dtype=torch.float32)
        #-------#

        count  = count  + 2
        print(f'{count} / {NUM_ITEMS}')
        #----#
    #--------#
    print(f'done!')
    print(f'casting params to fp16....')
    for key in lora: lora[f'{key}'] = lora[f'{key}'].to(device = device , dtype=torch.float16)
    #-------#
    print(f'done!')
    print(f'saving {savefile_name}...')
    save_file(lora , f'{savefile_name}')
#------#

new_rank = 16
new_alpha = math.floor(new_rank/2)
zero_threshold = 200 # e-6
name = 'tuff_nuff_camel'
a = load_file('/content/tuff.safetensors')
b = load_file('/content/nuff.safetensors')
c = load_file('/content/camel.safetensors')
savefile_name = f'{name}_{zero_threshold}_r{new_rank}_a{new_alpha}.safetensors'

count = 0
for key in a:
    a[f'{key}'] = a[f'{key}'].to(device = device , dtype = torch.float32)
    count = count + 1
print(f'num keys for a : {count}')
count = 0
for key in b:
    b[f'{key}'] = b[f'{key}'].to(device = device , dtype = torch.float32)
    count = count + 1
print(f'num keys for b : {count}')
count = 0
for key in c:
    c[f'{key}'] = c[f'{key}'].to(device = device , dtype = torch.float32)
    count = count + 1
print(f'num keys for c : {count}')

tgt = {}
#-----#
print(f'for {name}.safetensors at scale = (rank/alpha) = 0.5')
merge_and_save(b,c,a, savefile_name, new_rank , new_alpha, zero_threshold)

#filter_and_save(a , savefile_name, new_rank , new_alpha, zero_threshold)


In [ ]:
suffix = 'jpg'

for number in range(94):
  if number>20:break
  try:
    input_image = Image.open(f"/content/{number+1}.{suffix}").convert('RGB')
    caption = stream_chat(input_image, "descriptive", "formal", "any")
    print(f"...\n\n...caption for {number+1}.{suffix}\n\n...")
    print(caption)
  except:
    continue
#----#


Prompt: Describe the image in 400 words


/usr/local/lib/python3.10/dist-packages/bitsandbytes/autograd/_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


...

...caption for 22.jpg

...
This is a digital CGI rendering of a young woman with a realistic, hyper-detailed style. She has fair skin with a slight tan, and her long, straight black hair is pulled back into a high ponytail. Her eyes are a striking blue, accented with subtle eyeliner and mascara, and she has a calm, slightly serious expression with a hint of a smile. Her lips are full and naturally pink, with no lipstick.

She is wearing a black, strapless top made of a shiny, smooth material that looks like leather or vinyl. The top has a harness-style design with straps that crisscross over her chest and back, featuring metal rings and buckles that add to the edgy, gothic aesthetic. The straps are black, adding contrast to her pale skin.

The background is a simple gradient of dark gray and black, which makes the subject stand out. The lighting is soft and even, highlighting the contours of her face and body without casting any harsh shadows. The overall mood of the image is mode

In [ ]:
letter = 'B'
suffix = 'jpg'

for number in range(9):
  try:
    input_image = Image.open(f"/content/{letter} ({number+1}).{suffix}").convert('RGB')
    caption = stream_chat(input_image, "descriptive", "formal", "any")
    print(f"\n\ncaption for {letter}({number+1}).{suffix}\n\n")
    print(caption)
  except:
    x = 1
  #-----#

  try:
    suffix = 'webp'
    input_image = Image.open(f"/content/{letter} ({number+1}).{suffix}").convert('RGB')
    caption = stream_chat(input_image, "descriptive", "formal", "any")
    print(f"\n\ncaption for {letter}({number+1}).{suffix}\n\n")
    print(caption)
  except:
    continue
#------#

Prompt: Describe the image in 400 words


/usr/local/lib/python3.10/dist-packages/bitsandbytes/autograd/_functions.py:315: UserWarning: MatMul8bitLt: inputs will be cast from torch.bfloat16 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")




caption for B(1).jpg


A young Caucasian woman stands against a plain white backdrop, her long, wavy blonde hair cascading over her shoulders. She has a slender, toned physique with fair skin and a subtle tan. Her facial features are delicate, with arched eyebrows, full lips, and a slight, elegant nose. She is dressed in a dark teal blue bikini-style lingerie set, consisting of a bra and matching thong that accentuates her small to medium-sized breasts and flat stomach. The bra has thin straps and a minimalistic design, while the thong features a high waistband and a low-cut design that highlights her hips and buttocks. She is also wearing black lace-trimmed thigh-high stockings that add a touch of sensuality to her outfit. On her feet are black platform high heels with clear platform soles, adding height to her slender frame and giving her a confident, commanding presence. Around her neck is a black choker, adding to the overall sultry and provocative look of her ensemble. The photo

In [ ]:
letter = 'C'
suffix = 'jpg'

for number in range(9):
  try:
    input_image = Image.open(f"/content/{letter} ({number+1}).{suffix}").convert('RGB')
    caption = stream_chat(input_image, "descriptive", "formal", "any")
    print(f"\n\ncaption for {letter}({number+1}).{suffix}\n\n")
    print(caption)
  except:
    x = 1
  #-----#

  try:
    suffix = 'webp'
    input_image = Image.open(f"/content/{letter} ({number+1}).{suffix}").convert('RGB')
    caption = stream_chat(input_image, "descriptive", "formal", "any")
    print(f"\n\ncaption for {letter}({number+1}).{suffix}\n\n")
    print(caption)
  except:
    continue
#------#

Prompt: Describe the image in 400 words


caption for C(1).jpg


A young Caucasian woman with light skin and long, wavy blonde hair cascading over her shoulders stands indoors in a library or study. She has a slender physique, medium-sized breasts, and a flat stomach. Her expression is sultry, with her lips slightly parted and a seductive gaze directed at the camera.

She is dressed in a leather harness, which wraps around her body and leaves her bare from the waist up. The harness is brown with metal rings and buckles, adding a touch of BDSM to the scene. Her arms are restrained behind her back, with her hands gripping the leather straps, accentuating her bound state.

The background features a wooden bookshelf filled with various books, giving the room a scholarly vibe. The books are arranged in different colors and sizes, adding depth and texture to the background. The lighting is soft, highlighting the woman's features and the texture of the leather harness.

The overall mood of th

In [ ]:
letter = 'D'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

Prompt: Describe the image in 400 words


caption for D(1).jpg


A young woman stands in an outdoor, rustic setting with a wooden fence in the background. She is holding an assault rifle in her right hand, pointing it upward. The rifle has a bright purple muzzle and is painted with camouflage patterns. She is dressed in a military-style outfit, including a gray hoodie with the hood pulled up and camouflage pants with various patches and pockets. Her face is partially covered by a white mask with a black pattern, giving her a mysterious and tactical appearance. She wears black tactical gloves on her hands and black combat boots with thick soles.

The background features a wooden fence with the words "OP: FREE" painted in black letters. The fence is weathered and has a rustic texture. Behind the fence, there is a green metal structure that looks like a gate or a barrier. The area around the fence is covered in grass and rocks, with some patches of dirt and gravel. The sky is overcast, in

In [ ]:
letter = 'E'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

Prompt: Describe the image in 400 words


caption for E(1).jpg


A young woman in her early 20s is striking a pose in a swanky, elegant living room. She's kneeling on a plush, black and white damask couch with intricate floral patterns. Her long, straight, light brown hair is styled into two buns on either side of her head, with two cat ears attached to the top of her head. She's wearing a tight, sleeveless, white dress with a high slit on the right side, revealing her thigh and black stockings. The dress has a red sash around her waist and red ribbons tied at the hem, adding a touch of color to her outfit. She's also wearing black gloves and red high-heeled shoes with red straps.

In her hands, she holds a black gun, pointing it towards the camera, giving off a playful yet provocative vibe. Her expression is confident and slightly cheeky, with a hint of a smile. The background features a modern chandelier with crystal drops, adding a touch of glamour to the room. The walls are a light

In [ ]:
letter = 'F'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

Prompt: Describe the image in 400 words


caption for F(1).jpg


A young Asian woman stands in a dimly lit industrial setting, dressed in a dark outfit that includes a black blazer with a white collar, a black pleated skirt, and black knee-high socks. She has long, straight black hair with bangs, and she wears a stern expression. In her right hand, she holds a large, black assault rifle, and her left hand grips a bundle of yellow gloves.

The background features a large, complex control panel with numerous buttons, switches, and dials, indicating a high-tech or military environment. The control panel is mounted on a metal frame, and pipes and cables run across the ceiling, adding to the industrial feel. The lighting is harsh and focused, creating deep shadows and highlighting the textures of the woman's clothing and the control panel.

The woman's outfit and the setting suggest a scenario of high tension or urgency, possibly related to military or emergency operations. Her stance is co

In [ ]:
letter = 'G'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

Prompt: Describe the image in 400 words


caption for G(1).jpg


A black and white photograph of a person dressed in a tactical gear cosplay, standing against a plain background. The person has a slender build and is wearing a dark hooded tactical vest over a black long-sleeved shirt. The hood has several mesh panels and the vest is adorned with numerous pockets and straps, including a large pouch on the front and a hydration bladder on the left shoulder. The person is also wearing fingerless gloves, black shorts, and high-top tactical boots with thick soles. A tactical backpack is slung over one shoulder, and a large assault rifle is held diagonally across the body, with the muzzle pointed down. The rifle has a long barrel and a stock that extends to the ground, and it is equipped with various attachments, including a scope and a vertical grip.

The person's face is partially obscured by the hood and a mask with a menacing grin, giving a sinister and intimidating appearance. The mask 

In [ ]:
letter = 'H'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

Prompt: Describe the image in 400 words


caption for H(1).jpg


A young woman kneels on a concrete floor, with her back to the camera, in a dimly lit industrial setting. She has long, flowing red hair cascading down her back. She's dressed in a provocative, military-inspired outfit, featuring a black beret, a short, pleated black skirt with red stripes, and a black leather jacket with red accents. She's also wearing black thigh-high stockings with a garter belt and red suspenders that are attached to a black leather garter belt around her waist. The garter belt is partially unbuttoned, revealing her bare buttocks, which are prominently displayed due to her kneeling position. Her black leather boots have thick soles and a chunky heel, adding to the rugged, edgy look of her outfit.

In the background, there is a large, green industrial drum, and behind it, there is a partially open door revealing a fiery scene with orange and red flames and smoke, suggesting a dramatic or dangerous sett

In [ ]:
letter = 'I'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

Prompt: Describe the image in 400 words


caption for I(1).jpg


Two soldiers in a modern military setting are shown in a tense, intense moment. The soldier in the foreground is a woman with light skin and dark hair, wearing a helmet with a camouflage pattern. She's holding a rifle with both hands, her face grim and focused. Her eyes are hidden behind black-framed glasses, and she's dressed in a camouflage jacket over a tactical vest with pouches and straps, giving her a rugged and prepared look. A patch on her chest features a white logo.

Behind her, slightly to the right, stands another soldier, a man with a beard and glasses. He's also in a camo jacket and tactical vest, holding a similar rifle. He's positioned to the side, adding a sense of depth and action to the scene. The background is blurred, with a muted, industrial look, likely a warehouse or hangar, suggesting a realistic, combat-ready environment.

The textures in the image are varied, from the smooth surfaces of the helm

In [ ]:
letter = 'J'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

Prompt: Describe the image in 400 words


caption for J(1).jpg


A photograph featuring four women in a grand, ornate room with high ceilings and large, dark wooden pillars. The room is lit by soft, warm lights, casting a cozy glow on the polished wooden floor. The women are dressed in a mix of vintage and gothic-inspired outfits, adding to the scene's surreal and mysterious vibe.

The woman on the far left is sitting on the floor with her legs bent, wearing a sleeveless white dress with a delicate floral pattern and a high neckline. She holds a rifle across her lap, her gaze directed at the camera with a solemn expression.

The woman in the center is standing and holding a rifle across her chest. She has short, platinum blonde hair and wears a light pink lace dress with long sleeves, a high neckline, and a flowing skirt. Her expression is intense and focused.

The woman on the far right is kneeling on the floor, holding a rifle across her lap. She has long, blonde hair and wears a bla

In [ ]:
letter = 'K'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'L'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'M'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'N'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'O'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'P'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'Q'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'R'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'S'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'T'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'U'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'V'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'W'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'X'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)

In [ ]:
letter = 'Y'

for number in range(9):
  input_image = Image.open(f"/content/{letter} ({number+1}).jpg").convert('RGB')
  # caption type (descriptive/training_prompt/rng-tags)
  # caption tone (formal/informal)
  # caption length (any/very short/short/medium-length/long/very long or a specific number)
  caption = stream_chat(input_image, "descriptive", "formal", "any")
  print(f"\n\ncaption for {letter}({number+1}).jpg\n\n")
  print(caption)